# AVISO!

Recomendamos muito consultar a versão no github, onde os arquivos estão 
organizados corretamente. Além disso, alguns componentes de código encontram-se
em arquivos `.py`.

Link: <https://github.com/DanielHLelis/Neural-Nets-TP2>

## Authors

- D. H. Lelis - 12543822
- Samuel Veronez - 12542626
- Fernando Campos - 12542352

## Mudanças da Re-entrega

- Split entre teste e validação para o early stopping
- POS_WEIGHT baseado apenas nos dados de teste

# Exploring the Datasets

In [1]:
import os

import polars as pl
import plotly.express as px

from IPython.display import display

## Compress original data

In [2]:
ROOT_PATH = '../'

try:
    _olid_train = pl.read_csv(os.path.join(ROOT_PATH, "data/olid-br/train.csv"))
    _olid_train.write_parquet(os.path.join(ROOT_PATH, "data/olid-br/train.parquet.zstd"), compression="zstd", compression_level=9)

    _olid_test = pl.read_csv(os.path.join(ROOT_PATH, "data/olid-br/test.csv"))
    _olid_test.write_parquet(os.path.join(ROOT_PATH, "data/olid-br/test.parquet.zstd"), compression="zstd", compression_level=9)

    _told = pl.read_csv(os.path.join(ROOT_PATH, "data/told-br/told-br.csv"))
    _told.write_parquet(os.path.join(ROOT_PATH, "data/told-br/told-br.parquet.zstd"), compression="zstd", compression_level=9)
except:
    pass

## OLID-BR

### OLID-BR: Data Loading

In [3]:
olidbr_train = pl.read_parquet(os.path.join(ROOT_PATH, "data/olid-br/train.parquet.zstd"))
olidbr_test = pl.read_parquet(os.path.join(ROOT_PATH, "data/olid-br/test.parquet.zstd"))

In [4]:
# Join the train and test datasets
olidbr = pl.concat([olidbr_train, olidbr_test])

# Display 5 random samples
olidbr.sample(5, seed=42)

shape: (5, 17)
┌────────────┬────────────┬────────────┬────────────┬───┬────────┬────────────┬────────┬───────────┐
│ id         ┆ text       ┆ is_offensi ┆ is_targete ┆ … ┆ racism ┆ religious_ ┆ sexism ┆ xenophobi │
│ ---        ┆ ---        ┆ ve         ┆ d          ┆   ┆ ---    ┆ intoleranc ┆ ---    ┆ a         │
│ str        ┆ str        ┆ ---        ┆ ---        ┆   ┆ bool   ┆ e          ┆ bool   ┆ ---       │
│            ┆            ┆ str        ┆ str        ┆   ┆        ┆ ---        ┆        ┆ bool      │
│            ┆            ┆            ┆            ┆   ┆        ┆ bool       ┆        ┆           │
╞════════════╪════════════╪════════════╪════════════╪═══╪════════╪════════════╪════════╪═══════════╡
│ 92882c2101 ┆ Muita      ┆ OFF        ┆ UNT        ┆ … ┆ false  ┆ false      ┆ false  ┆ false     │
│ 08475ba3af ┆ merda      ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ 23a2a10a4e ┆            ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ …          ┆            ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ 81ddfdb7d9 ┆ USER de    ┆ OFF        ┆ TIN        ┆ … ┆ false  ┆ false      ┆ false  ┆ false     │
│ 7442f29e78 ┆ idade não  ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ 08531e6aa2 ┆ pode       ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ …          ┆ respond…   ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ 6c07f22150 ┆ RIDICULA,  ┆ OFF        ┆ TIN        ┆ … ┆ false  ┆ false      ┆ false  ┆ false     │
│ fd41f4a54e ┆ USER USER, ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ fbfaf30bd2 ┆ PREPOTENT… ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ …          ┆            ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ a9edcee25e ┆ USER       ┆ NOT        ┆ UNT        ┆ … ┆ false  ┆ false      ┆ false  ┆ false     │
│ 5a409a8ef6 ┆ mesmo,     ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ 6c603d89ed ┆ porque até ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ …          ┆ os anos…   ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ 2989149634 ┆ lixo       ┆ OFF        ┆ UNT        ┆ … ┆ false  ┆ false      ┆ false  ┆ false     │
│ 8a4638841f ┆ total, uma ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ c59db34821 ┆ propaganda ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
│ …          ┆ des…       ┆            ┆            ┆   ┆        ┆            ┆        ┆           │
└────────────┴────────────┴────────────┴────────────┴───┴────────┴────────────┴────────┴───────────┘

### OLID-BR: Data Distribution

In [5]:
print("OLID-BR Train")
print(olidbr_train['is_offensive'].value_counts())

print("OLID-BR Test")
print(olidbr_test['is_offensive'].value_counts())

print("OLID-BR Full")
print(olidbr['is_offensive'].value_counts())


OLID-BR Train
shape: (2, 2)
┌──────────────┬───────┐
│ is_offensive ┆ count │
│ ---          ┆ ---   │
│ str          ┆ u32   │
╞══════════════╪═══════╡
│ OFF          ┆ 4452  │
│ NOT          ┆ 762   │
└──────────────┴───────┘
OLID-BR Test
shape: (2, 2)
┌──────────────┬───────┐
│ is_offensive ┆ count │
│ ---          ┆ ---   │
│ str          ┆ u32   │
╞══════════════╪═══════╡
│ OFF          ┆ 1484  │
│ NOT          ┆ 254   │
└──────────────┴───────┘
OLID-BR Full
shape: (2, 2)
┌──────────────┬───────┐
│ is_offensive ┆ count │
│ ---          ┆ ---   │
│ str          ┆ u32   │
╞══════════════╪═══════╡
│ NOT          ┆ 1016  │
│ OFF          ┆ 5936  │
└──────────────┴───────┘


In [6]:
px.histogram(
    olidbr, 
    x='is_offensive', 
    color='is_offensive', 
    title='OLID-BR Offensive Distribution', 
    template='plotly_dark',
).show()

### Reclassify Offensiveness

In [7]:
# Recompiling the dataset with the sum of all offensive categories
olidbr_recompiled = olidbr.with_columns([
    pl.sum_horizontal(
        pl.col("profanity_obscene"), 
        pl.col("health"), 
        pl.col("ideology"), 
        pl.col("insult"), 
        pl.col("lgbtqphobia"), 
        pl.col("other_lifestyle"), 
        pl.col("physical_aspects"), 
        pl.col("racism"), 
        pl.col("religious_intolerance"), 
        pl.col("sexism"), 
        pl.col("xenophobia"),
    ).alias("offensive"),
    pl.sum_horizontal(
        pl.col("health"), 
        pl.col("ideology"), 
        pl.col("insult"), 
        pl.col("lgbtqphobia"), 
        pl.col("other_lifestyle"), 
        pl.col("physical_aspects"), 
        pl.col("racism"), 
        pl.col("religious_intolerance"), 
        pl.col("sexism"), 
        pl.col("xenophobia"),
    ).alias("offensive_allow_profane")
])

olidbr_recompiled = olidbr_recompiled.with_columns(
    [
        pl.when(pl.col("offensive") > 0).then(True).otherwise(False).alias("offensive_discrete"),
        pl.when(pl.col("offensive_allow_profane") > 0).then(True).otherwise(False).alias("offensive_allow_profane_discrete"),
    ]
)

In [8]:
olidbr_recompiled.sample(5, seed=42)

shape: (5, 21)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ id        ┆ text      ┆ is_offens ┆ is_target ┆ … ┆ offensive ┆ offensive ┆ offensive ┆ offensiv │
│ ---       ┆ ---       ┆ ive       ┆ ed        ┆   ┆ ---       ┆ _allow_pr ┆ _discrete ┆ e_allow_ │
│ str       ┆ str       ┆ ---       ┆ ---       ┆   ┆ u32       ┆ ofane     ┆ ---       ┆ profane_ │
│           ┆           ┆ str       ┆ str       ┆   ┆           ┆ ---       ┆ bool      ┆ discre…  │
│           ┆           ┆           ┆           ┆   ┆           ┆ u32       ┆           ┆ ---      │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ bool     │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 92882c210 ┆ Muita     ┆ OFF       ┆ UNT       ┆ … ┆ 1         ┆ 1         ┆ true      ┆ true     │
│ 108475ba3 ┆ merda     ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ af23a2a10 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ a4e…      ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 81ddfdb7d ┆ USER de   ┆ OFF       ┆ TIN       ┆ … ┆ 1         ┆ 1         ┆ true      ┆ true     │
│ 97442f29e ┆ idade não ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 7808531e6 ┆ pode      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ aa2…      ┆ respond…  ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 6c07f2215 ┆ RIDICULA, ┆ OFF       ┆ TIN       ┆ … ┆ 1         ┆ 1         ┆ true      ┆ true     │
│ 0fd41f4a5 ┆ USER      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 4efbfaf30 ┆ USER, PRE ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ bd2…      ┆ POTENT…   ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ a9edcee25 ┆ USER      ┆ NOT       ┆ UNT       ┆ … ┆ 0         ┆ 0         ┆ false     ┆ false    │
│ e5a409a8e ┆ mesmo,    ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ f66c603d8 ┆ porque    ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 9ed…      ┆ até os    ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆ anos…     ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 298914963 ┆ lixo      ┆ OFF       ┆ UNT       ┆ … ┆ 1         ┆ 1         ┆ true      ┆ true     │
│ 48a463884 ┆ total,    ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 1fc59db34 ┆ uma propa ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 821…      ┆ ganda     ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆ des…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [9]:
print("OLID-BR Recompiled")
print(olidbr_recompiled['offensive_discrete'].value_counts())

print("OLID-BR Recompiled (Allow Profane)")
print(olidbr_recompiled['offensive_allow_profane_discrete'].value_counts())

OLID-BR Recompiled
shape: (2, 2)
┌────────────────────┬───────┐
│ offensive_discrete ┆ count │
│ ---                ┆ ---   │
│ bool               ┆ u32   │
╞════════════════════╪═══════╡
│ false              ┆ 1027  │
│ true               ┆ 5925  │
└────────────────────┴───────┘
OLID-BR Recompiled (Allow Profane)
shape: (2, 2)
┌─────────────────────────────────┬───────┐
│ offensive_allow_profane_discre… ┆ count │
│ ---                             ┆ ---   │
│ bool                            ┆ u32   │
╞═════════════════════════════════╪═══════╡
│ true                            ┆ 5680  │
│ false                           ┆ 1272  │
└─────────────────────────────────┴───────┘


#### An overview of the balance of the dataset

As we can see, the dataset is very unbalanced towards offensive comments. 
Because of such, we might merge it with other datasets for a better balance.

## ToLD-Br

### ToLD-Br: Data Loading

FYI, the data is classified by offense type, with the values from 0 to 3,
indicating the number of times the comment was classified as offensive.


In [10]:
toldbr = pl.read_parquet(os.path.join(ROOT_PATH, "data/told-br/told-br.parquet.zstd"))

In [11]:
toldbr.sample(5, seed=42)

shape: (5, 7)
┌─────────────────────────────────┬────────────┬─────────┬────────┬────────┬──────────┬────────────┐
│ text                            ┆ homophobia ┆ obscene ┆ insult ┆ racism ┆ misogyny ┆ xenophobia │
│ ---                             ┆ ---        ┆ ---     ┆ ---    ┆ ---    ┆ ---      ┆ ---        │
│ str                             ┆ f64        ┆ f64     ┆ f64    ┆ f64    ┆ f64      ┆ f64        │
╞═════════════════════════════════╪════════════╪═════════╪════════╪════════╪══════════╪════════════╡
│ 8 demais porra                  ┆ 0.0        ┆ 2.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        │
│ rt @user @user felizmente os s… ┆ 0.0        ┆ 0.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        │
│ caralho tandara #voleinaglobo … ┆ 0.0        ┆ 1.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        │
│ vamo c calma mo                 ┆ 0.0        ┆ 0.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        │
│                                 ┆            ┆         ┆        ┆        ┆          ┆            │
│ nosso filho v…                  ┆            ┆         ┆        ┆        ┆          ┆            │
│ que puta sentimento lixo. quer… ┆ 0.0        ┆ 0.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        │
└─────────────────────────────────┴────────────┴─────────┴────────┴────────┴──────────┴────────────┘

### ToLD-Br: Data Distribution

In [12]:
px.histogram(
    toldbr,
    x=['homophobia', 'obscene', 'insult', 'racism', 'misogyny', 'xenophobia'],
    title='ToLD-Br Category Classification Distribution', 
    template='plotly_dark',
).show()

In [13]:
toldbr_off = toldbr.with_columns([
    pl.sum_horizontal(
        pl.col('homophobia'), 
        pl.col('obscene'), 
        pl.col('insult'), 
        pl.col('racism'), 
        pl.col('misogyny'), 
        pl.col('xenophobia'),
    ).alias('offensive'),
])

In [14]:
toldbr_off.sample(5, seed=42)

shape: (5, 8)
┌─────────────────────┬────────────┬─────────┬────────┬────────┬──────────┬────────────┬───────────┐
│ text                ┆ homophobia ┆ obscene ┆ insult ┆ racism ┆ misogyny ┆ xenophobia ┆ offensive │
│ ---                 ┆ ---        ┆ ---     ┆ ---    ┆ ---    ┆ ---      ┆ ---        ┆ ---       │
│ str                 ┆ f64        ┆ f64     ┆ f64    ┆ f64    ┆ f64      ┆ f64        ┆ f64       │
╞═════════════════════╪════════════╪═════════╪════════╪════════╪══════════╪════════════╪═══════════╡
│ 8 demais porra      ┆ 0.0        ┆ 2.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        ┆ 2.0       │
│ rt @user @user      ┆ 0.0        ┆ 0.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        ┆ 0.0       │
│ felizmente os s…    ┆            ┆         ┆        ┆        ┆          ┆            ┆           │
│ caralho tandara     ┆ 0.0        ┆ 1.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        ┆ 1.0       │
│ #voleinaglobo …     ┆            ┆         ┆        ┆        ┆          ┆            ┆           │
│ vamo c calma mo     ┆ 0.0        ┆ 0.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        ┆ 0.0       │
│                     ┆            ┆         ┆        ┆        ┆          ┆            ┆           │
│ nosso filho v…      ┆            ┆         ┆        ┆        ┆          ┆            ┆           │
│ que puta sentimento ┆ 0.0        ┆ 0.0     ┆ 0.0    ┆ 0.0    ┆ 0.0      ┆ 0.0        ┆ 0.0       │
│ lixo. quer…         ┆            ┆         ┆        ┆        ┆          ┆            ┆           │
└─────────────────────┴────────────┴─────────┴────────┴────────┴──────────┴────────────┴───────────┘

In [15]:
px.histogram(
    toldbr_off,
    x='offensive',
    color='offensive',
    title='ToLD-Br Offensive Distribution', 
    template='plotly_dark',
).show()

In [16]:
toldbr_class_threshold = 1

toldbr_discrete = toldbr_off.with_columns([
    pl.when(pl.col('offensive') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_offensive_low'),
    pl.when(pl.col('homophobia') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_homophobia_low'),
    pl.when(pl.col('obscene') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_obscene_low'),
    pl.when(pl.col('insult') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_insult_low'),
    pl.when(pl.col('racism') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_racism_low'),
    pl.when(pl.col('misogyny') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_misogyny_low'),
    pl.when(pl.col('xenophobia') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_xenophobia_low'),
])

toldbr_class_threshold = 2
toldbr_discrete = toldbr_discrete.with_columns([
    pl.when(pl.col('offensive') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_offensive_high'),
    pl.when(pl.col('homophobia') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_homophobia_high'),
    pl.when(pl.col('obscene') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_obscene_high'),
    pl.when(pl.col('insult') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_insult_high'),
    pl.when(pl.col('racism') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_racism_high'),
    pl.when(pl.col('misogyny') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_misogyny_high'),
    pl.when(pl.col('xenophobia') >= toldbr_class_threshold).
        then(True).
        otherwise(False).
        alias('is_xenophobia_high'),
]).select([
    'text', 'is_offensive_low', 
    'is_homophobia_low', 'is_obscene_low', 'is_insult_low', 
    'is_racism_low', 'is_misogyny_low', 'is_xenophobia_low',
    'is_offensive_high', 'is_homophobia_high', 'is_obscene_high', 
    'is_insult_high', 'is_racism_high', 'is_misogyny_high', 'is_xenophobia_high',
])


In [17]:
toldbr_discrete.sample(5, seed=42)

shape: (5, 15)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ text      ┆ is_offens ┆ is_homoph ┆ is_obscen ┆ … ┆ is_insult ┆ is_racism ┆ is_misogy ┆ is_xenop │
│ ---       ┆ ive_low   ┆ obia_low  ┆ e_low     ┆   ┆ _high     ┆ _high     ┆ ny_high   ┆ hobia_hi │
│ str       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ gh       │
│           ┆ bool      ┆ bool      ┆ bool      ┆   ┆ bool      ┆ bool      ┆ bool      ┆ ---      │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ bool     │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 8 demais  ┆ true      ┆ false     ┆ true      ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ porra     ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ rt @user  ┆ false     ┆ false     ┆ false     ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ @user fel ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ izmente   ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ os s…     ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ caralho   ┆ true      ┆ false     ┆ true      ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ tandara   ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ #voleinag ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ lobo …    ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ vamo c    ┆ false     ┆ false     ┆ false     ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ calma mo  ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ nosso     ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ filho v…  ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ que puta  ┆ false     ┆ false     ┆ false     ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ sentiment ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ o lixo.   ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ quer…     ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [18]:
print("ToLD-BR (At least 1 flag)")
print(toldbr_discrete['is_offensive_low'].value_counts())

print("ToLD-BR (At least 2 flags)")
print(toldbr_discrete['is_offensive_high'].value_counts())

ToLD-BR (At least 1 flag)
shape: (2, 2)
┌──────────────────┬───────┐
│ is_offensive_low ┆ count │
│ ---              ┆ ---   │
│ bool             ┆ u32   │
╞══════════════════╪═══════╡
│ true             ┆ 9255  │
│ false            ┆ 11745 │
└──────────────────┴───────┘
ToLD-BR (At least 2 flags)
shape: (2, 2)
┌───────────────────┬───────┐
│ is_offensive_high ┆ count │
│ ---               ┆ ---   │
│ bool              ┆ u32   │
╞═══════════════════╪═══════╡
│ true              ┆ 4816  │
│ false             ┆ 16184 │
└───────────────────┴───────┘


In [19]:
px.histogram(
    toldbr_discrete,
    x='is_offensive_low',
    color='is_offensive_low',
    title='ToLD-Br Offensive Distribution (Discrete Low)', 
    template='plotly_dark',
).show()

px.histogram(
    toldbr_discrete,
    x='is_offensive_high',
    color='is_offensive_high',
    title='ToLD-Br Offensive Distribution (Discrete High)', 
    template='plotly_dark',
).show()

#### An overview of the balance of the dataset

This dataset is way more balanced, when compared to OLID-BR. But, there is a
slight issue with the criteria, it seems. There aren't filtering for profanity
and it seems like one of the labelers considered profanit as obscene, while
the others, not.

When going for a stricter filter, we might use the "Low" variant, while for a
more relaxed one, we might use the "High" variant.

## Simplifying the datasets

In [20]:
olidbr_recompiled.sample(5, seed=42)

shape: (5, 21)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ id        ┆ text      ┆ is_offens ┆ is_target ┆ … ┆ offensive ┆ offensive ┆ offensive ┆ offensiv │
│ ---       ┆ ---       ┆ ive       ┆ ed        ┆   ┆ ---       ┆ _allow_pr ┆ _discrete ┆ e_allow_ │
│ str       ┆ str       ┆ ---       ┆ ---       ┆   ┆ u32       ┆ ofane     ┆ ---       ┆ profane_ │
│           ┆           ┆ str       ┆ str       ┆   ┆           ┆ ---       ┆ bool      ┆ discre…  │
│           ┆           ┆           ┆           ┆   ┆           ┆ u32       ┆           ┆ ---      │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ bool     │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 92882c210 ┆ Muita     ┆ OFF       ┆ UNT       ┆ … ┆ 1         ┆ 1         ┆ true      ┆ true     │
│ 108475ba3 ┆ merda     ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ af23a2a10 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ a4e…      ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 81ddfdb7d ┆ USER de   ┆ OFF       ┆ TIN       ┆ … ┆ 1         ┆ 1         ┆ true      ┆ true     │
│ 97442f29e ┆ idade não ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 7808531e6 ┆ pode      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ aa2…      ┆ respond…  ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 6c07f2215 ┆ RIDICULA, ┆ OFF       ┆ TIN       ┆ … ┆ 1         ┆ 1         ┆ true      ┆ true     │
│ 0fd41f4a5 ┆ USER      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 4efbfaf30 ┆ USER, PRE ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ bd2…      ┆ POTENT…   ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ a9edcee25 ┆ USER      ┆ NOT       ┆ UNT       ┆ … ┆ 0         ┆ 0         ┆ false     ┆ false    │
│ e5a409a8e ┆ mesmo,    ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ f66c603d8 ┆ porque    ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 9ed…      ┆ até os    ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆ anos…     ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 298914963 ┆ lixo      ┆ OFF       ┆ UNT       ┆ … ┆ 1         ┆ 1         ┆ true      ┆ true     │
│ 48a463884 ┆ total,    ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 1fc59db34 ┆ uma propa ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 821…      ┆ ganda     ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆ des…      ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [21]:
toldbr_discrete.sample(5, seed=42)

shape: (5, 15)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ text      ┆ is_offens ┆ is_homoph ┆ is_obscen ┆ … ┆ is_insult ┆ is_racism ┆ is_misogy ┆ is_xenop │
│ ---       ┆ ive_low   ┆ obia_low  ┆ e_low     ┆   ┆ _high     ┆ _high     ┆ ny_high   ┆ hobia_hi │
│ str       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ gh       │
│           ┆ bool      ┆ bool      ┆ bool      ┆   ┆ bool      ┆ bool      ┆ bool      ┆ ---      │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ bool     │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 8 demais  ┆ true      ┆ false     ┆ true      ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ porra     ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ rt @user  ┆ false     ┆ false     ┆ false     ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ @user fel ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ izmente   ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ os s…     ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ caralho   ┆ true      ┆ false     ┆ true      ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ tandara   ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ #voleinag ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ lobo …    ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ vamo c    ┆ false     ┆ false     ┆ false     ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ calma mo  ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ nosso     ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ filho v…  ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ que puta  ┆ false     ┆ false     ┆ false     ┆ … ┆ false     ┆ false     ┆ false     ┆ false    │
│ sentiment ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ o lixo.   ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ quer…     ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [22]:
toldbr_final = toldbr_discrete.select([
    pl.lit('ToLD-Br').alias('dataset'),
    pl.col('text').hash().alias('id').cast(pl.String),
    pl.col('text').str.replace_all('@user', 'USER'), # Replace @user with USER, to match OLID-BR
    pl.col('is_offensive_low').alias('off_strict'),
    pl.col('is_offensive_high').alias('off_relaxed'),
])
toldbr_final.sample(5, seed=42)

shape: (5, 5)
┌─────────┬──────────────────────┬─────────────────────────────────┬────────────┬─────────────┐
│ dataset ┆ id                   ┆ text                            ┆ off_strict ┆ off_relaxed │
│ ---     ┆ ---                  ┆ ---                             ┆ ---        ┆ ---         │
│ str     ┆ str                  ┆ str                             ┆ bool       ┆ bool        │
╞═════════╪══════════════════════╪═════════════════════════════════╪════════════╪═════════════╡
│ ToLD-Br ┆ 12559603335008373494 ┆ 8 demais porra                  ┆ true       ┆ true        │
│ ToLD-Br ┆ 1455693542618679752  ┆ rt USER USER felizmente os sol… ┆ false      ┆ false       │
│ ToLD-Br ┆ 17500462964768468320 ┆ caralho tandara #voleinaglobo … ┆ true       ┆ false       │
│ ToLD-Br ┆ 2818557597701017591  ┆ vamo c calma mo                 ┆ false      ┆ false       │
│         ┆                      ┆                                 ┆            ┆             │
│         ┆                      ┆ nosso filho v…                  ┆            ┆             │
│ ToLD-Br ┆ 14538197625843834331 ┆ que puta sentimento lixo. quer… ┆ false      ┆ false       │
└─────────┴──────────────────────┴─────────────────────────────────┴────────────┴─────────────┘

In [23]:
olidbr_final = olidbr_recompiled.select([
    pl.lit('OLID-Br').alias('dataset'),
    pl.col('id').cast(pl.String),
    'text',
    pl.col('offensive_discrete').alias('off_strict'),
    pl.col('offensive_allow_profane_discrete').alias('off_relaxed'),
])
olidbr_final.sample(5, seed=42)

shape: (5, 5)
┌─────────┬──────────────────────────────┬──────────────────────────────┬────────────┬─────────────┐
│ dataset ┆ id                           ┆ text                         ┆ off_strict ┆ off_relaxed │
│ ---     ┆ ---                          ┆ ---                          ┆ ---        ┆ ---         │
│ str     ┆ str                          ┆ str                          ┆ bool       ┆ bool        │
╞═════════╪══════════════════════════════╪══════════════════════════════╪════════════╪═════════════╡
│ OLID-Br ┆ 92882c210108475ba3af23a2a10a ┆ Muita merda                  ┆ true       ┆ true        │
│         ┆ 4e…                          ┆                              ┆            ┆             │
│ OLID-Br ┆ 81ddfdb7d97442f29e7808531e6a ┆ USER de idade não pode       ┆ true       ┆ true        │
│         ┆ a2…                          ┆ respond…                     ┆            ┆             │
│ OLID-Br ┆ 6c07f22150fd41f4a54efbfaf30b ┆ RIDICULA, USER USER,         ┆ true       ┆ true        │
│         ┆ d2…                          ┆ PREPOTENT…                   ┆            ┆             │
│ OLID-Br ┆ a9edcee25e5a409a8ef66c603d89 ┆ USER mesmo, porque até os    ┆ false      ┆ false       │
│         ┆ ed…                          ┆ anos…                        ┆            ┆             │
│ OLID-Br ┆ 29891496348a4638841fc59db348 ┆ lixo total, uma propaganda   ┆ true       ┆ true        │
│         ┆ 21…                          ┆ des…                         ┆            ┆             │
└─────────┴──────────────────────────────┴──────────────────────────────┴────────────┴─────────────┘

In [24]:
final_dataset = pl.concat([toldbr_final, olidbr_final])
final_dataset.sample(5, seed=534)

shape: (5, 5)
┌─────────┬──────────────────────────────┬──────────────────────────────┬────────────┬─────────────┐
│ dataset ┆ id                           ┆ text                         ┆ off_strict ┆ off_relaxed │
│ ---     ┆ ---                          ┆ ---                          ┆ ---        ┆ ---         │
│ str     ┆ str                          ┆ str                          ┆ bool       ┆ bool        │
╞═════════╪══════════════════════════════╪══════════════════════════════╪════════════╪═════════════╡
│ ToLD-Br ┆ 9322321234464027338          ┆ pérola tá terrível , ela se  ┆ true       ┆ false       │
│         ┆                              ┆ ac…                          ┆            ┆             │
│ ToLD-Br ┆ 17106631069393288087         ┆ USER parabéns pela coragem   ┆ true       ┆ true        │
│         ┆                              ┆ pq …                         ┆            ┆             │
│ ToLD-Br ┆ 12766216725703474573         ┆ rt USER porra eu chorei      ┆ true       ┆ false       │
│         ┆                              ┆ demais…                      ┆            ┆             │
│ OLID-Br ┆ 88aacb3db46a4ff8a70b563cc9e5 ┆ USER Evoluiu...antes comia   ┆ true       ┆ true        │
│         ┆ 0f…                          ┆ tra…                         ┆            ┆             │
│ OLID-Br ┆ 878d1939c62e4658a6697d20535d ┆ O presidente é quem manda no ┆ true       ┆ true        │
│         ┆ cb…                          ┆ p…                           ┆            ┆             │
└─────────┴──────────────────────────────┴──────────────────────────────┴────────────┴─────────────┘

In [25]:
# Write the dataset
os.makedirs(os.path.join(ROOT_PATH, "data/joint"), exist_ok=True)
final_dataset.write_parquet(os.path.join(ROOT_PATH, "data/joint/data.parquet.zstd"), compression="zstd", compression_level=9)

In [26]:
px.histogram(
    final_dataset,
    x='off_strict',
    color='off_strict',
    title='Final Offensive Distribution (Strict)', 
    template='plotly_dark',
).show()

In [27]:
px.histogram(
    final_dataset,
    x='off_relaxed',
    color='off_relaxed',
    title='Final Offensive Distribution (Relaxed)', 
    template='plotly_dark',
).show()

# Dataset Preprocessing

In [38]:
import os
import sys
import re

import polars as pl
from tqdm.notebook import tqdm
from IPython.display import clear_output

import nltk
import spacy
import unidecode

In [2]:
ROOT_PATH = '../'
DRIVE_PATH = 'Colab/ToxicityClassification'

# When on Colab, use Google Drive as the root path to persist and load data
if 'google.colab' in sys.modules:
    from google.colab import drive
    drive.mount('/content/drive')
    ROOT_PATH = os.path.join('/content/drive/My Drive/', DRIVE_PATH)
    os.makedirs(ROOT_PATH, exist_ok=True)
    os.chdir(ROOT_PATH)

## Load Dataset

In [3]:
df = pl.read_parquet(os.path.join(ROOT_PATH, 'data', 'joint', 'data.parquet.zstd'))

## Setup Toolkits

In [7]:
nltk.download('punkt')
spacy.cli.download('pt_core_news_sm')
clear_output()

In [30]:
nlp = spacy.load('pt_core_news_sm')

## Normalize

In [39]:
cleanup_re = re.compile(r'[\W\s]')
remove_double_spaces_re = re.compile(r'\s+')

base_clean = []
base_clean_lower = []
tokenized = []
lemmatized = []
no_accents = []
lemma_no_accents = []
no_stop_words = []
lemma_no_stop_words = []
no_stop_words_no_accents = []
lemma_no_stop_words_no_accents = []


# TODO: generalize each pre-processing approach into a separate function
# in a separate file.
for row in tqdm(df.iter_rows(named=True), total=len(df)):
    text: str = row['text']
    # Remove bad characters
    text = cleanup_re.sub(' ', text)
    text = remove_double_spaces_re.sub(' ', text)
    text = text.strip()
    base_clean.append(text)

    # Lowercase
    text = text.lower()
    base_clean_lower.append(text)

    # Tokenize
    # TODO: go deeper into tokenization
    tokens = [token for token in nlp(text)]
    tokenized.append([token.text for token in tokens])

    # Lemmatized
    lemmatized.append([token.lemma_ for token in tokens])

    # No accents
    no_accents.append([unidecode.unidecode(token.text) for token in tokens])
    lemma_no_accents.append([unidecode.unidecode(token.lemma_) for token in tokens])

    # No stop words
    no_stop_words.append([token.text for token in tokens if not token.is_stop])
    lemma_no_stop_words.append([token.lemma_ for token in tokens if not token.is_stop])

    # No stop words, no accents
    no_stop_words_no_accents.append([unidecode.unidecode(token.text) for token in tokens if not token.is_stop])
    lemma_no_stop_words_no_accents.append([unidecode.unidecode(token.lemma_) for token in tokens if not token.is_stop])



df_ext = df.with_columns([
    pl.Series('base_clean', base_clean),
    pl.Series('base_clean_lower', base_clean_lower),
    pl.Series('tokenized', tokenized),
    pl.Series('lemmatized', lemmatized),
    pl.Series('no_accents', no_accents),
    pl.Series('lemma_no_accents', lemma_no_accents),
    pl.Series('no_stop_words', no_stop_words),
    pl.Series('lemma_no_stop_words', lemma_no_stop_words),
    pl.Series('no_stop_words_no_accents', no_stop_words_no_accents),
    pl.Series('lemma_no_stop_words_no_accents', lemma_no_stop_words_no_accents)
])

  0%|          | 0/27952 [00:00<?, ?it/s]

In [41]:
df_ext.write_parquet(os.path.join(ROOT_PATH, "data/joint/pre_processed_data.parquet.zstd"), compression="zstd", compression_level=9)

In [1]:
import os
import sys
import json
import random
from datetime import datetime

import numpy as np
import polars as pl
import plotly.express as px

from sklearn.model_selection import train_test_split

import torch
from torch import nn, optim, cuda
from torch.utils.data import DataLoader

In [2]:
ROOT_PATH = '../'
DRIVE_PATH = 'Colab/ToxicityClassification'

# When on Colab, use Google Drive as the root path to persist and load data
if 'google.colab' in sys.modules:
    from google.colab import drive
    drive.mount('/content/drive')
    ROOT_PATH = os.path.join('/content/drive/My Drive/', DRIVE_PATH)
    os.makedirs(ROOT_PATH, exist_ok=True)
    os.chdir(ROOT_PATH)

In [3]:

# Register the parent directory of the current script as a package root,
# so that we can import modules from the parent directory
sys.path.append(os.path.abspath(os.path.join(ROOT_PATH, 'src')))

from toxicity.training import train_epochs, model_metrics
from toxicity.bow.training import trainer, validate
from toxicity.bow.model import BoWModel, BoWDataset

## Setup

In [4]:
# Target device for running the model
PYTORCH_DEVICE = 'cuda' if cuda.is_available() else 'cpu'

# Random Seed
RANDOM_SEED = 777

# Training & Validation configs
TRAIN_RATIO = 0.8
TRAIN_BATCH_SIZE = 16
TEST_BATCH_SIZE = 16
EPOCHS = 20
LEARNING_RATE = 1.8e-05
# Will be overriden bellow
POS_WEIGHT = 1.663


OCC_TRESHOLD = 10
OTHER_TOKEN = '[OTHER]'
MAX_LEN = 256

print(f'Using device: {PYTORCH_DEVICE}')

Using device: cuda


In [5]:
def reseed(seed: int = RANDOM_SEED):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

reseed()

## Data Loading

In [6]:
df = pl.read_parquet(os.path.join(ROOT_PATH, 'data', 'joint', 'pre_processed_data.parquet.zstd'))
df = df.with_columns(
    df['off_relaxed'].cast(pl.Int32).cast(pl.List(pl.Int32)).cast(pl.Array(pl.Int32, 1)),
    df['off_strict'].cast(pl.Int32).cast(pl.List(pl.Int32)).cast(pl.Array(pl.Int32, 1)),
)
df.sample(5, seed=RANDOM_SEED)

#TODO: shall I balance?

shape: (5, 15)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ dataset ┆ id         ┆ text      ┆ off_stric ┆ … ┆ no_stop_w ┆ lemma_no_ ┆ no_stop_w ┆ lemma_no_ │
│ ---     ┆ ---        ┆ ---       ┆ t         ┆   ┆ ords      ┆ stop_word ┆ ords_no_a ┆ stop_word │
│ str     ┆ str        ┆ str       ┆ ---       ┆   ┆ ---       ┆ s         ┆ ccents    ┆ s_no_acce │
│         ┆            ┆           ┆ array[i32 ┆   ┆ list[str] ┆ ---       ┆ ---       ┆ nts       │
│         ┆            ┆           ┆ , 1]      ┆   ┆           ┆ list[str] ┆ list[str] ┆ ---       │
│         ┆            ┆           ┆           ┆   ┆           ┆           ┆           ┆ list[str] │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ ToLD-Br ┆ 1764398477 ┆ caralho q ┆ [1]       ┆ … ┆ ["caralho ┆ ["caralho ┆ ["caralho ┆ ["caralho │
│         ┆ 1725418028 ┆ vergonha  ┆           ┆   ┆ ", "q", … ┆ ", "q", … ┆ ", "q", … ┆ ", "q", … │
│         ┆            ┆ kkkkk     ┆           ┆   ┆ "kkkkk"]  ┆ "kkkkk"]  ┆ "kkkkk"]  ┆ "kkkkk"]  │
│ ToLD-Br ┆ 3886050625 ┆ foda-se,  ┆ [1]       ┆ … ┆ ["foda",  ┆ ["foda",  ┆ ["foda",  ┆ ["foda",  │
│         ┆ 220892585  ┆ vou       ┆           ┆   ┆ "vou", …  ┆ "ir", …   ┆ "vou", …  ┆ "ir", …   │
│         ┆            ┆ encher o  ┆           ┆   ┆ "lol"]    ┆ "lol"]    ┆ "lol"]    ┆ "lol"]    │
│         ┆            ┆ cu de po… ┆           ┆   ┆           ┆           ┆           ┆           │
│ ToLD-Br ┆ 1493609503 ┆ USER USER ┆ [1]       ┆ … ┆ ["user",  ┆ ["user",  ┆ ["user",  ┆ ["user",  │
│         ┆ 0342170465 ┆ USER Vc   ┆           ┆   ┆ "user", … ┆ "user", … ┆ "user", … ┆ "user", … │
│         ┆            ┆ só pensa  ┆           ┆   ┆ "esperta" ┆ "esperto" ┆ "esperta" ┆ "esperto" │
│         ┆            ┆ no …      ┆           ┆   ┆ ]         ┆ ]         ┆ ]         ┆ ]         │
│ ToLD-Br ┆ 1827925907 ┆ família   ┆ [0]       ┆ … ┆ ["família ┆ ["família ┆ ["familia ┆ ["familia │
│         ┆ 4216789411 ┆           ┆           ┆   ┆ "]        ┆ "]        ┆ "]        ┆ "]        │
│ OLID-Br ┆ 7f36b160e8 ┆ RT USER:  ┆ [0]       ┆ … ┆ ["rt",    ┆ ["rt",    ┆ ["rt",    ┆ ["rt",    │
│         ┆ 624968a32e ┆ vey a     ┆           ┆   ┆ "user", … ┆ "user", … ┆ "user", … ┆ "user", … │
│         ┆ 82b1c6750f ┆ juliette  ┆           ┆   ┆ "t"]      ┆ "t"]      ┆ "t"]      ┆ "t"]      │
│         ┆ …          ┆ veio c…   ┆           ┆   ┆           ┆           ┆           ┆           │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

## Setup Vocabulary for BoW

In [7]:
TIMESTAMP = datetime.now().strftime('%Y%m%d%H%M%S')
MODEL_PATH = os.path.join(ROOT_PATH, 'models', 'bow', TIMESTAMP)
os.makedirs(MODEL_PATH, exist_ok=True)

# Count frequency of tokens
occurences = {}
for tokens in df['lemma_no_stop_words_no_accents']:
    for t in tokens:
        if t not in occurences:
            occurences[t] = 1
        else:
            occurences[t] += 1
            
# Sort by frequency
occurences = dict(sorted(occurences.items(), key=lambda item: item[1], reverse=True))

# Build vocabulary
vocabulary = []
for w, counter in occurences.items():
    if counter > OCC_TRESHOLD:
        vocabulary.append(w)

# Sort vocabulary and add a token for other words
vocabulary = sorted(vocabulary)
vocabulary.append(OTHER_TOKEN)

# Vocabulary lookup table
vocab_index = {}
for i, token in enumerate(vocabulary):
    vocab_index[token] = i

# Write vocabulary to file
with open(os.path.join(MODEL_PATH, 'vocab.txt'), 'w') as f:
    f.write('\n'.join(vocabulary))
with open(os.path.join(MODEL_PATH, 'vocab_index.json'), 'w') as f:
    json.dump(vocab_index, f)
with open(os.path.join(MODEL_PATH, 'vocab.json'), 'w') as f:
    json.dump(vocabulary, f)

print(f'Vocabulary size: {len(vocabulary)}')

Vocabulary size: 2832


## Init Model

### Loss and Optimizer

Using a Binary Cross Entropy loss as it shows good results for binary classification tasks. We are also applying differente weights to the positive and negative classes to account for the class imbalance.

Adam optimizer is also used as it is a good general optimizer for training neural networks.

In [8]:
model = BoWModel(len(vocabulary))
model.to(PYTORCH_DEVICE)

loss_fn = nn.BCEWithLogitsLoss(pos_weight=torch.tensor([POS_WEIGHT], device=PYTORCH_DEVICE))
optimizer = optim.AdamW(params=model.parameters(), lr=LEARNING_RATE)

## Data Split

In [9]:
train_df, other_df = train_test_split(df, train_size=TRAIN_RATIO, random_state=RANDOM_SEED)
validate_df, test_df = train_test_split(other_df, train_size=0.5, random_state=RANDOM_SEED)


train_loader = DataLoader(
    BoWDataset(train_df, 'lemma_no_stop_words_no_accents', 'off_relaxed', vocab_index=vocab_index), 
    shuffle=True, num_workers=0, batch_size=TRAIN_BATCH_SIZE,
)
test_loader = DataLoader(
    BoWDataset(test_df, 'lemma_no_stop_words_no_accents', 'off_relaxed', vocab_index=vocab_index), 
    shuffle=False, num_workers=0, batch_size=TEST_BATCH_SIZE,
)
validate_loader = DataLoader(
    BoWDataset(validate_df, 'lemma_no_stop_words_no_accents', 'off_relaxed', vocab_index=vocab_index), 
    shuffle=False, num_workers=0, batch_size=TEST_BATCH_SIZE,
)

train_distribution = train_df['off_relaxed'].to_pandas().value_counts()
neg_count, pos_count = train_distribution.iloc[0], train_distribution.iloc[1]
print(f'Training distribution: {neg_count} negative, {pos_count} positive')
POS_WEIGHT = neg_count / pos_count
print(f'Positive weight: {POS_WEIGHT}')

Training distribution: 13932 negative, 8429 positive
Positive weight: 1.6528651085538024


## Training

In [10]:
def validate_result(loader: DataLoader, model: nn.Module):
    # Validate the results
    raw_results, raw_targets = validate(model, loader, PYTORCH_DEVICE)
    raw_results = np.array(raw_results)
    raw_targets = np.array(raw_targets)

    # Apply a fixed threshold to the results
    FIXED_THRESHOLD = 0.5
    fixed_results = raw_results > FIXED_THRESHOLD
    fixed_targets = raw_targets > FIXED_THRESHOLD

    # Compute metrics
    metrics = model_metrics(fixed_targets, fixed_results)
    return metrics

### Training Loop

In [11]:
CHECKPOINT_PATH = os.path.join(ROOT_PATH, 'checkpoints', 'bow', TIMESTAMP)
MODEL_PATH = os.path.join(ROOT_PATH, 'models', 'bow', TIMESTAMP)
BEST_MODEL_PATH = os.path.join(MODEL_PATH, 'best_model.pt')
os.makedirs(CHECKPOINT_PATH, exist_ok=True)
os.makedirs(MODEL_PATH, exist_ok=True)

loss_history = []
metric_history = []
test_metric_history = []

target_metric = ('Weighted F2', 'weighted_f2')
best_metric = float('-inf')
best_epoch = 0

# Save the best model; Override checkpoints; Track metrics
def epoch_callback(epoch, avg_loss):
    global loss_history, metric_history, test_metric_history, target_metric, best_metric, best_epoch
    
    metrics = validate_result(validate_loader, model)
    loss_history.append(avg_loss)
    metric_history.append(metrics)
    test_metrics = validate_result(test_loader, model)
    test_metric_history.append(test_metrics)

    print(f'Epoch {epoch+1}: Loss: {avg_loss:.4f}')
    print(f'Validation {target_metric[0]}: {metrics[target_metric[1]]:.4f}')
    print(f'Test {target_metric[0]}: {test_metrics[target_metric[1]]:.4f}')
    
    if metrics[target_metric[1]] > best_metric:
        print(f'New best model found!')
        best_metric = metrics[target_metric[1]]
        best_epoch = epoch
        torch.save(model, BEST_MODEL_PATH)
    
    

train_epochs(
    trainer, EPOCHS, model, train_loader, loss_fn, optimizer, PYTORCH_DEVICE,
    checkpoint_path=CHECKPOINT_PATH, epoch_callback=epoch_callback)

Running training epoch 1/20


  0%|          | 0/1398 [00:00<?, ?it/s]

  0%|          | 0/175 [00:00<?, ?it/s]

  0%|          | 0/175 [00:00<?, ?it/s]

Epoch 1: Loss: 0.8197
Validation Weighted F2: 0.7333
Test Weighted F2: 0.7297
New best model found!
Finished training epoch 1/20; Average Loss: 0.8197
Running training epoch 2/20


...

Epoch 19: Loss: 0.1050
Validation Weighted F2: 0.7510
Test Weighted F2: 0.7444
Finished training epoch 19/20; Average Loss: 0.1050
Running training epoch 20/20


  0%|          | 0/1398 [00:00<?, ?it/s]

  0%|          | 0/175 [00:00<?, ?it/s]

  0%|          | 0/175 [00:00<?, ?it/s]

Epoch 20: Loss: 0.1003
Validation Weighted F2: 0.7528
Test Weighted F2: 0.7477
Finished training epoch 20/20; Average Loss: 0.1003


In [14]:
# Build result metrics data frame per epoch
result_df = pl.DataFrame({
    'epoch': range(1, len(loss_history) + 1),
    'loss': loss_history,
}).with_columns(pl.from_dicts(metric_history))

test_result_df = pl.DataFrame({
    'epoch': range(1, len(loss_history) + 1),
}).with_columns(pl.from_dicts(test_metric_history))

result_df.head()

shape: (5, 9)
┌───────┬──────────┬─────────────┬──────────┬───┬──────────┬──────────┬──────────┬───────────┐
│ epoch ┆ loss     ┆ weighted_f1 ┆ macro_f1 ┆ … ┆ macro_f2 ┆ accuracy ┆ recall   ┆ precision │
│ ---   ┆ ---      ┆ ---         ┆ ---      ┆   ┆ ---      ┆ ---      ┆ ---      ┆ ---       │
│ i64   ┆ f64      ┆ f64         ┆ f64      ┆   ┆ f64      ┆ f64      ┆ f64      ┆ f64       │
╞═══════╪══════════╪═════════════╪══════════╪═══╪══════════╪══════════╪══════════╪═══════════╡
│ 1     ┆ 0.819739 ┆ 0.734673    ┆ 0.719554 ┆ … ┆ 0.721758 ┆ 0.732737 ┆ 0.732737 ┆ 0.738097  │
│ 2     ┆ 0.649648 ┆ 0.772676    ┆ 0.757188 ┆ … ┆ 0.75654  ┆ 0.773166 ┆ 0.773166 ┆ 0.772284  │
│ 3     ┆ 0.566674 ┆ 0.776574    ┆ 0.762052 ┆ … ┆ 0.76232  ┆ 0.776386 ┆ 0.776386 ┆ 0.776779  │
│ 4     ┆ 0.517649 ┆ 0.778839    ┆ 0.763837 ┆ … ┆ 0.763264 ┆ 0.779249 ┆ 0.779249 ┆ 0.778503  │
│ 5     ┆ 0.477843 ┆ 0.779802    ┆ 0.764755 ┆ … ┆ 0.764027 ┆ 0.780322 ┆ 0.780322 ┆ 0.779402  │
└───────┴──────────┴─────────────┴──────────┴───┴──────────┴──────────┴──────────┴───────────┘

In [13]:
# Plot Loss and Target Metric per Epoch, highlighting the peak
fig_a = px.line(result_df, x='epoch', y='loss', title='Loss per Epoch', template='plotly_dark')
fig_a.add_scatter(x=[best_epoch+1], y=[loss_history[best_epoch]], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_a.update_layout()
fig_a.show()

fig_b = px.line(result_df, x='epoch', y='weighted_f2', title='Validation Weighted F2 per Epoch', template='plotly_dark')
fig_b.add_scatter(x=[best_epoch+1], y=[metric_history[best_epoch]['weighted_f2']], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_b.update_layout()
fig_b.show()

fig_c = px.line(test_result_df, x='epoch', y='weighted_f2', title='Test Weighted F2 per Epoch', template='plotly_dark')
fig_c.add_scatter(x=[best_epoch+1], y=[test_metric_history[best_epoch]['weighted_f2']], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_c.update_layout()
fig_c.show()

In [1]:
import os
import sys
import random
from datetime import datetime

import numpy as np
import polars as pl
import plotly.express as px

from sklearn.model_selection import train_test_split

import torch
from torch import nn, optim, cuda
from torch.utils.data import DataLoader

In [2]:
ROOT_PATH = '../'
DRIVE_PATH = 'Colab/ToxicityClassification'

# When on Colab, use Google Drive as the root path to persist and load data
if 'google.colab' in sys.modules:
    from google.colab import drive
    drive.mount('/content/drive')
    ROOT_PATH = os.path.join('/content/drive/My Drive/', DRIVE_PATH)
    os.makedirs(ROOT_PATH, exist_ok=True)
    os.chdir(ROOT_PATH)

In [3]:
# Register the parent directory of the current script as a package root,
# so that we can import modules from the parent directory
sys.path.append(os.path.abspath(os.path.join(ROOT_PATH, 'src')))

from toxicity.training import train_epochs, model_metrics
from toxicity.embeddings.training import trainer, validate
from toxicity.embeddings.model import EmbeddingModel, EmbeddingDataset

## Setup

In [4]:
# Target device for running the model
PYTORCH_DEVICE = 'cuda' if cuda.is_available() else 'cpu'

# Random Seed
RANDOM_SEED = 777

# Training & Validation configs
TRAIN_RATIO = 0.8
TRAIN_BATCH_SIZE = 16
TEST_BATCH_SIZE = 16
EPOCHS = 20
LEARNING_RATE = 1.8e-05
POS_WEIGHT = 1.663


EMBEDDING_FILE = os.path.join(ROOT_PATH, 'cbow_s100.txt')
EMBEDDING_NAME = 'cbow_s100'
MAX_LEN = 128

print(f'Using device: {PYTORCH_DEVICE}')

Using device: cuda


In [5]:

def reseed(seed: int = RANDOM_SEED):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

reseed()

## Data Loading

In [6]:
df = pl.read_parquet(os.path.join(ROOT_PATH, 'data', 'joint', 'pre_processed_data.parquet.zstd'))
df = df.with_columns(
    df['off_relaxed'].cast(pl.Int32).cast(pl.List(pl.Int32)).cast(pl.Array(pl.Int32, 1)),
    df['off_strict'].cast(pl.Int32).cast(pl.List(pl.Int32)).cast(pl.Array(pl.Int32, 1)),
)
df.sample(5, seed=RANDOM_SEED)

shape: (5, 15)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ dataset ┆ id         ┆ text      ┆ off_stric ┆ … ┆ no_stop_w ┆ lemma_no_ ┆ no_stop_w ┆ lemma_no_ │
│ ---     ┆ ---        ┆ ---       ┆ t         ┆   ┆ ords      ┆ stop_word ┆ ords_no_a ┆ stop_word │
│ str     ┆ str        ┆ str       ┆ ---       ┆   ┆ ---       ┆ s         ┆ ccents    ┆ s_no_acce │
│         ┆            ┆           ┆ array[i32 ┆   ┆ list[str] ┆ ---       ┆ ---       ┆ nts       │
│         ┆            ┆           ┆ , 1]      ┆   ┆           ┆ list[str] ┆ list[str] ┆ ---       │
│         ┆            ┆           ┆           ┆   ┆           ┆           ┆           ┆ list[str] │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ ToLD-Br ┆ 1764398477 ┆ caralho q ┆ [1]       ┆ … ┆ ["caralho ┆ ["caralho ┆ ["caralho ┆ ["caralho │
│         ┆ 1725418028 ┆ vergonha  ┆           ┆   ┆ ", "q", … ┆ ", "q", … ┆ ", "q", … ┆ ", "q", … │
│         ┆            ┆ kkkkk     ┆           ┆   ┆ "kkkkk"]  ┆ "kkkkk"]  ┆ "kkkkk"]  ┆ "kkkkk"]  │
│ ToLD-Br ┆ 3886050625 ┆ foda-se,  ┆ [1]       ┆ … ┆ ["foda",  ┆ ["foda",  ┆ ["foda",  ┆ ["foda",  │
│         ┆ 220892585  ┆ vou       ┆           ┆   ┆ "vou", …  ┆ "ir", …   ┆ "vou", …  ┆ "ir", …   │
│         ┆            ┆ encher o  ┆           ┆   ┆ "lol"]    ┆ "lol"]    ┆ "lol"]    ┆ "lol"]    │
│         ┆            ┆ cu de po… ┆           ┆   ┆           ┆           ┆           ┆           │
│ ToLD-Br ┆ 1493609503 ┆ USER USER ┆ [1]       ┆ … ┆ ["user",  ┆ ["user",  ┆ ["user",  ┆ ["user",  │
│         ┆ 0342170465 ┆ USER Vc   ┆           ┆   ┆ "user", … ┆ "user", … ┆ "user", … ┆ "user", … │
│         ┆            ┆ só pensa  ┆           ┆   ┆ "esperta" ┆ "esperto" ┆ "esperta" ┆ "esperto" │
│         ┆            ┆ no …      ┆           ┆   ┆ ]         ┆ ]         ┆ ]         ┆ ]         │
│ ToLD-Br ┆ 1827925907 ┆ família   ┆ [0]       ┆ … ┆ ["família ┆ ["família ┆ ["familia ┆ ["familia │
│         ┆ 4216789411 ┆           ┆           ┆   ┆ "]        ┆ "]        ┆ "]        ┆ "]        │
│ OLID-Br ┆ 7f36b160e8 ┆ RT USER:  ┆ [0]       ┆ … ┆ ["rt",    ┆ ["rt",    ┆ ["rt",    ┆ ["rt",    │
│         ┆ 624968a32e ┆ vey a     ┆           ┆   ┆ "user", … ┆ "user", … ┆ "user", … ┆ "user", … │
│         ┆ 82b1c6750f ┆ juliette  ┆           ┆   ┆ "t"]      ┆ "t"]      ┆ "t"]      ┆ "t"]      │
│         ┆ …          ┆ veio c…   ┆           ┆   ┆           ┆           ┆           ┆           │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

### Load Embeddings

In [7]:
EMBEDDING_PATH = os.path.join(ROOT_PATH, 'models', f'embeddings-{EMBEDDING_NAME}')
os.makedirs(EMBEDDING_PATH, exist_ok=True)

emb_dim = None
token_count = None
embeddings = {}

if not os.path.exists(f'{EMBEDDING_PATH}/embeddings.parquet.zstd'):
    with open(EMBEDDING_FILE, 'r') as f:
        fl = f.readline()
        token_count, emb_dim = map(int, fl.split(' '))

        while line := f.readline():
            emb = line.split(' ')

            token = emb[0]
            values = [float(v) for v in emb[1:]]

            if emb_dim is None:
                emb_dim = len(values)
            elif emb_dim != len(values):
                raise ValueError('Inconsistent embedding length')

            embeddings[token] = values
    
    print(f'Embedding Length: {emb_dim}')
    print(f'Embedding Vocab Size: {len(embeddings)}; Expected: {token_count}')
    embedding_df = pl.DataFrame({
        'token': list(embeddings.keys()),
        'embedding': list(embeddings.values())
    })
    embedding_df.write_parquet(f'{EMBEDDING_PATH}/embeddings.parquet.zstd', compression="zstd", compression_level=9)
else:
    embedding_df = pl.read_parquet(f'{EMBEDDING_PATH}/embeddings.parquet.zstd')
    token_list = embedding_df['token'].to_list()
    embedding_list = embedding_df['embedding'].to_list()
    embeddings = dict(zip(token_list, embedding_list))
    emb_dim = len(embeddings[next(iter(embeddings))])
    token_count = len(embeddings)
    print(f'Embedding Length: {emb_dim}')
    print(f'Embedding Vocab Size: {len(embeddings)}; Expected: {token_count}')


Embedding Length: 100
Embedding Vocab Size: 929606; Expected: 929606


## Init Model

### Loss and Optimizer

Using a Binary Cross Entropy loss as it shows good results for binary classification tasks. We are also applying differente weights to the positive and negative classes to account for the class imbalance.

Adam optimizer is also used as it is a good general optimizer for training neural networks.

In [8]:
model = EmbeddingModel(emb_dim, MAX_LEN)
model.to(PYTORCH_DEVICE)

loss_fn = nn.BCEWithLogitsLoss(pos_weight=torch.tensor([POS_WEIGHT], device=PYTORCH_DEVICE))
optimizer = optim.AdamW(params=model.parameters(), lr=LEARNING_RATE)

## Data Split

In [9]:
train_df, other_df = train_test_split(df, train_size=TRAIN_RATIO, random_state=RANDOM_SEED)
validate_df, test_df = train_test_split(other_df, train_size=0.5, random_state=RANDOM_SEED)

train_loader = DataLoader(
    EmbeddingDataset(train_df, 'lemma_no_stop_words', 'off_relaxed', embeddings=embeddings, emb_dim=emb_dim, seq_len=MAX_LEN), 
    shuffle=True, num_workers=0, batch_size=TRAIN_BATCH_SIZE,
)
test_loader = DataLoader(
    EmbeddingDataset(test_df, 'lemma_no_stop_words', 'off_relaxed', embeddings=embeddings, emb_dim=emb_dim, seq_len=MAX_LEN), 
    shuffle=False, num_workers=0, batch_size=TEST_BATCH_SIZE,
)
validate_loader = DataLoader(
    EmbeddingDataset(validate_df, 'lemma_no_stop_words', 'off_relaxed', embeddings=embeddings, emb_dim=emb_dim, seq_len=MAX_LEN), 
    shuffle=False, num_workers=0, batch_size=TEST_BATCH_SIZE,
)

train_distribution = train_df['off_relaxed'].to_pandas().value_counts()
neg_count, pos_count = train_distribution.iloc[0], train_distribution.iloc[1]
print(f'Training distribution: {neg_count} negative, {pos_count} positive')
POS_WEIGHT = neg_count / pos_count
print(f'Positive weight: {POS_WEIGHT}')

Training distribution: 13932 negative, 8429 positive
Positive weight: 1.6528651085538024


## Training

In [10]:
def validate_result(loader: DataLoader, model: nn.Module):
    # Validate the results
    raw_results, raw_targets = validate(model, loader, PYTORCH_DEVICE)
    raw_results = np.array(raw_results)
    raw_targets = np.array(raw_targets)

    # Apply a fixed threshold to the results
    FIXED_THRESHOLD = 0.5
    fixed_results = raw_results > FIXED_THRESHOLD
    fixed_targets = raw_targets > FIXED_THRESHOLD

    # Compute metrics
    metrics = model_metrics(fixed_targets, fixed_results)
    return metrics

### Training Loop

In [11]:
TIMESTAMP = datetime.now().strftime('%Y%m%d%H%M%S')
MODEL_PATH = os.path.join(ROOT_PATH, 'models', f'embeddings-{EMBEDDING_NAME}', TIMESTAMP)
BEST_MODEL_PATH = os.path.join(MODEL_PATH, 'best_model.pt')
CHECKPOINT_PATH = os.path.join(ROOT_PATH, 'checkpoints', f'embeddings-{EMBEDDING_NAME}', TIMESTAMP)
os.makedirs(CHECKPOINT_PATH, exist_ok=True)
os.makedirs(MODEL_PATH, exist_ok=True)

loss_history = []
metric_history = []
test_metric_history = []
target_metric = ('Weighted F2', 'weighted_f2')
best_metric = float('-inf')
best_epoch = 0

# Save the best model; Override checkpoints; Track metrics
def epoch_callback(epoch, avg_loss):
    global loss_history, metric_history, test_metric_history, target_metric, best_metric, best_epoch
    
    metrics = validate_result(validate_loader, model)
    loss_history.append(avg_loss)
    metric_history.append(metrics)
    test_metrics = validate_result(test_loader, model)
    test_metric_history.append(test_metrics)

    print(f'Epoch {epoch+1}: Loss: {avg_loss:.4f}')
    print(f'Validation {target_metric[0]}: {metrics[target_metric[1]]:.4f}')
    print(f'Test {target_metric[0]}: {test_metrics[target_metric[1]]:.4f}')
    
    if metrics[target_metric[1]] > best_metric:
        print(f'New best model found!')
        best_metric = metrics[target_metric[1]]
        best_epoch = epoch
        torch.save(model, BEST_MODEL_PATH)



train_epochs(
    trainer, EPOCHS, model, train_loader, loss_fn, optimizer, PYTORCH_DEVICE,
    checkpoint_path=CHECKPOINT_PATH, epoch_callback=epoch_callback)

Running training epoch 1/20


  0%|          | 0/1398 [00:00<?, ?it/s]

  0%|          | 0/175 [00:00<?, ?it/s]

  0%|          | 0/175 [00:00<?, ?it/s]

Epoch 1: Loss: 0.8217
Validation Weighted F2: 0.6255
Test Weighted F2: 0.6190
New best model found!
Finished training epoch 1/20; Average Loss: 0.8217
Running training epoch 2/20


...

Epoch 19: Loss: 0.1180
Validation Weighted F2: 0.6815
Test Weighted F2: 0.6797
Finished training epoch 19/20; Average Loss: 0.1180
Running training epoch 20/20


  0%|          | 0/1398 [00:00<?, ?it/s]

  0%|          | 0/175 [00:00<?, ?it/s]

  0%|          | 0/175 [00:00<?, ?it/s]

Epoch 20: Loss: 0.1131
Validation Weighted F2: 0.6793
Test Weighted F2: 0.6800
Finished training epoch 20/20; Average Loss: 0.1131


In [12]:
# Build result metrics data frame per epoch
result_df = pl.DataFrame({
    'epoch': range(1, len(loss_history) + 1),
    'loss': loss_history,
}).with_columns(pl.from_dicts(metric_history))

test_result_df = pl.DataFrame({
    'epoch': range(1, len(loss_history) + 1),
}).with_columns(pl.from_dicts(test_metric_history))

result_df.head()


shape: (5, 9)
┌───────┬──────────┬─────────────┬──────────┬───┬──────────┬──────────┬──────────┬───────────┐
│ epoch ┆ loss     ┆ weighted_f1 ┆ macro_f1 ┆ … ┆ macro_f2 ┆ accuracy ┆ recall   ┆ precision │
│ ---   ┆ ---      ┆ ---         ┆ ---      ┆   ┆ ---      ┆ ---      ┆ ---      ┆ ---       │
│ i64   ┆ f64      ┆ f64         ┆ f64      ┆   ┆ f64      ┆ f64      ┆ f64      ┆ f64       │
╞═══════╪══════════╪═════════════╪══════════╪═══╪══════════╪══════════╪══════════╪═══════════╡
│ 1     ┆ 0.821739 ┆ 0.633112    ┆ 0.626195 ┆ … ┆ 0.635294 ┆ 0.628265 ┆ 0.628265 ┆ 0.676534  │
│ 2     ┆ 0.730445 ┆ 0.686137    ┆ 0.670944 ┆ … ┆ 0.674477 ┆ 0.68229  ┆ 0.68229  ┆ 0.695327  │
│ 3     ┆ 0.689854 ┆ 0.687161    ┆ 0.67122  ┆ … ┆ 0.674221 ┆ 0.683721 ┆ 0.683721 ┆ 0.694494  │
│ 4     ┆ 0.65406  ┆ 0.69952     ┆ 0.679777 ┆ … ┆ 0.679818 ┆ 0.699463 ┆ 0.699463 ┆ 0.699578  │
│ 5     ┆ 0.61356  ┆ 0.694634    ┆ 0.676868 ┆ … ┆ 0.678434 ┆ 0.692665 ┆ 0.692665 ┆ 0.697648  │
└───────┴──────────┴─────────────┴──────────┴───┴──────────┴──────────┴──────────┴───────────┘

In [13]:
# Plot Loss and Target Metric per Epoch, highlighting the peak
fig_a = px.line(result_df, x='epoch', y='loss', title='Loss per Epoch', template='plotly_dark')
fig_a.add_scatter(x=[best_epoch+1], y=[loss_history[best_epoch]], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_a.update_layout()
fig_a.show()

fig_b = px.line(result_df, x='epoch', y='weighted_f2', title='Validation Weighted F2 per Epoch', template='plotly_dark')
fig_b.add_scatter(x=[best_epoch+1], y=[metric_history[best_epoch]['weighted_f2']], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_b.update_layout()
fig_b.show()

fig_c = px.line(test_result_df, x='epoch', y='weighted_f2', title='Test Weighted F2 per Epoch', template='plotly_dark')
fig_c.add_scatter(x=[best_epoch+1], y=[test_metric_history[best_epoch]['weighted_f2']], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_c.update_layout()
fig_c.show()

# Neural Solution - Transformers: BERT

In [1]:
import os
import sys
import random
from datetime import datetime

import numpy as np
import polars as pl
import plotly.express as px
from sklearn.model_selection import train_test_split

import torch
from torch import nn, optim, cuda
from torch.utils.data import DataLoader

In [2]:
ROOT_PATH = '../'
DRIVE_PATH = 'Colab/ToxicityClassification'

# When on Colab, use Google Drive as the root path to persist and load data
if 'google.colab' in sys.modules:
    from google.colab import drive
    drive.mount('/content/drive')
    ROOT_PATH = os.path.join('/content/drive/My Drive/', DRIVE_PATH)
    os.makedirs(ROOT_PATH, exist_ok=True)
    os.chdir(ROOT_PATH)

In [3]:
# Register the parent directory of the current script as a package root,
# so that we can import modules from the parent directory
sys.path.append(os.path.abspath(os.path.join(ROOT_PATH, 'src')))

from toxicity.transformers.bertimbau_base import bert_tokenizer, BertDatasetBF16, BertModuleBF16
from toxicity.transformers.training import trainer, validate
from toxicity.training import train_epochs, model_metrics

## Setup

In [4]:
# Target device for running the model
PYTORCH_DEVICE = 'cuda' if cuda.is_available() else 'cpu'

# Random Seed
RANDOM_SEED = 777

# Training & Validation configs
TRAIN_RATIO = 0.8
MAX_LEN = 256
TRAIN_BATCH_SIZE = 32
TEST_BATCH_SIZE = 32
EPOCHS = 20
LEARNING_RATE = 3e-05
POS_WEIGHT = 1.663

print(f'Using device: {PYTORCH_DEVICE}')

Using device: cuda


In [5]:
random.seed(RANDOM_SEED)
np.random.seed(RANDOM_SEED)
torch.manual_seed(RANDOM_SEED)
torch.cuda.manual_seed_all(RANDOM_SEED)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

## Data Loading

In [6]:
df = pl.read_parquet(os.path.join(ROOT_PATH, 'data', 'joint', 'pre_processed_data.parquet.zstd'))
df = df.with_columns(
    df['off_relaxed'].cast(pl.Int32).cast(pl.List(pl.Int32)).cast(pl.Array(pl.Int32, 1)),
    df['off_strict'].cast(pl.Int32).cast(pl.List(pl.Int32)).cast(pl.Array(pl.Int32, 1)),
)
df.sample(5, seed=42)

shape: (5, 15)
┌─────────┬────────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ dataset ┆ id         ┆ text      ┆ off_stric ┆ … ┆ no_stop_w ┆ lemma_no_ ┆ no_stop_w ┆ lemma_no_ │
│ ---     ┆ ---        ┆ ---       ┆ t         ┆   ┆ ords      ┆ stop_word ┆ ords_no_a ┆ stop_word │
│ str     ┆ str        ┆ str       ┆ ---       ┆   ┆ ---       ┆ s         ┆ ccents    ┆ s_no_acce │
│         ┆            ┆           ┆ array[i32 ┆   ┆ list[str] ┆ ---       ┆ ---       ┆ nts       │
│         ┆            ┆           ┆ , 1]      ┆   ┆           ┆ list[str] ┆ list[str] ┆ ---       │
│         ┆            ┆           ┆           ┆   ┆           ┆           ┆           ┆ list[str] │
╞═════════╪════════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ ToLD-Br ┆ 5508727285 ┆ medo de   ┆ [0]       ┆ … ┆ ["medo",  ┆ ["medo",  ┆ ["medo",  ┆ ["medo",  │
│         ┆ 226739644  ┆ ir pra um ┆           ┆   ┆ "pra", …  ┆ "pra", …  ┆ "pra", …  ┆ "pra", …  │
│         ┆            ┆ rolê de   ┆           ┆   ┆ "kkkkkkk" ┆ "kkkkkkk" ┆ "kkkkkkk" ┆ "kkkkkkk" │
│         ┆            ┆ novo…     ┆           ┆   ┆ ]         ┆ ]         ┆ ]         ┆ ]         │
│ ToLD-Br ┆ 1682784190 ┆ https://t ┆ [0]       ┆ … ┆ ["https", ┆ ["https", ┆ ["https", ┆ ["https", │
│         ┆ 3506270139 ┆ .co/2bs6o ┆           ┆   ┆ "t", …    ┆ "t", …    ┆ "t", …    ┆ "t", …    │
│         ┆            ┆ D330q     ┆           ┆   ┆ "gd2j98vr ┆ "gd2j98vr ┆ "gd2j98vr ┆ "gd2j98vr │
│         ┆            ┆           ┆           ┆   ┆ kg"]      ┆ kg"]      ┆ kg"]      ┆ kg"]      │
│         ┆            ┆ Ele a…    ┆           ┆   ┆           ┆           ┆           ┆           │
│ ToLD-Br ┆ 7641628880 ┆ rt USER   ┆ [0]       ┆ … ┆ ["rt",    ┆ ["rt",    ┆ ["rt",    ┆ ["rt",    │
│         ┆ 024884135  ┆ bruno     ┆           ┆   ┆ "user", … ┆ "user", … ┆ "user", … ┆ "user", … │
│         ┆            ┆ fernandes ┆           ┆   ┆ "user"]   ┆ "user"]   ┆ "user"]   ┆ "user"]   │
│         ┆            ┆ assina…   ┆           ┆   ┆           ┆           ┆           ┆           │
│ ToLD-Br ┆ 1686624250 ┆ tinha que ┆ [1]       ┆ … ┆ ["tinha", ┆ ["ter",   ┆ ["tinha", ┆ ["ter",   │
│         ┆ 8514532033 ┆ ter       ┆           ┆   ┆ "jogado", ┆ "jogar",  ┆ "jogado", ┆ "jogar",  │
│         ┆            ┆ jogado    ┆           ┆   ┆ … "trem"] ┆ … "tr"]   ┆ … "trem"] ┆ … "tr"]   │
│         ┆            ┆ esse      ┆           ┆   ┆           ┆           ┆           ┆           │
│         ┆            ┆ bran…     ┆           ┆   ┆           ┆           ┆           ┆           │
│ ToLD-Br ┆ 3068271252 ┆ eu sou a  ┆ [0]       ┆ … ┆ ["pessoa" ┆ ["pessoa" ┆ ["pessoa" ┆ ["pessoa" │
│         ┆ 403811869  ┆ pessoa    ┆           ┆   ┆ ,         ┆ ,         ┆ ,         ┆ ,         │
│         ┆            ┆ certa no  ┆           ┆   ┆ "certa",  ┆ "certo",  ┆ "certa",  ┆ "certo",  │
│         ┆            ┆ bairr…    ┆           ┆   ┆ …         ┆ …         ┆ …         ┆ …         │
│         ┆            ┆           ┆           ┆   ┆ "errado"… ┆ "errar"]  ┆ "errado"… ┆ "errar"]  │
└─────────┴────────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

## Setup Model

In [7]:
tokenizer = bert_tokenizer()

model = BertModuleBF16(feature_count=1)
model.to(PYTORCH_DEVICE)

BertModuleBF16(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(29794, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwis

## Data Split

In [8]:

train_df, other_df = train_test_split(df, train_size=TRAIN_RATIO, random_state=RANDOM_SEED)
validate_df, test_df = train_test_split(other_df, train_size=0.5, random_state=RANDOM_SEED)

train_loader = DataLoader(
    BertDatasetBF16(data_frame=train_df, tokenizer=tokenizer, max_len=MAX_LEN, target_col='off_relaxed'), 
    shuffle=True, num_workers=0, batch_size=TRAIN_BATCH_SIZE,
)
test_loader = DataLoader(
    BertDatasetBF16(data_frame=test_df, tokenizer=tokenizer, max_len=MAX_LEN, target_col='off_relaxed'), 
    shuffle=False, num_workers=0, batch_size=TEST_BATCH_SIZE,
)
validate_loader = DataLoader(
    BertDatasetBF16(data_frame=validate_df, tokenizer=tokenizer, max_len=MAX_LEN, target_col='off_relaxed'), 
    shuffle=False, num_workers=0, batch_size=TEST_BATCH_SIZE,
)

train_distribution = train_df['off_relaxed'].to_pandas().value_counts()
neg_count, pos_count = train_distribution.iloc[0], train_distribution.iloc[1]
print(f'Training distribution: {neg_count} negative, {pos_count} positive')
POS_WEIGHT = neg_count / pos_count
print(f'Positive weight: {POS_WEIGHT}')

Training distribution: 13932 negative, 8429 positive
Positive weight: 1.6528651085538024


### Loss and Optimizer

Using a Binary Cross Entropy loss as it shows good results for binary classification tasks. We are also applying differente weights to the positive and negative classes to account for the class imbalance.

Adam optimizer is also used as it is a good general optimizer for training neural networks, with good known results for BERT models.

In [9]:
loss_fn = nn.BCEWithLogitsLoss(pos_weight=torch.tensor([POS_WEIGHT], device=PYTORCH_DEVICE))
optimizer = optim.AdamW(params=model.parameters(), lr=LEARNING_RATE)

### Training

### Result Validation

In [10]:
def validate_result(loader: DataLoader, model: nn.Module):
    # Validate the results
    raw_results, raw_targets = validate(model, loader, PYTORCH_DEVICE)
    raw_results = np.array(raw_results)
    raw_targets = np.array(raw_targets)

    # Apply a fixed threshold to the results
    FIXED_THRESHOLD = 0.5
    fixed_results = raw_results > FIXED_THRESHOLD
    fixed_targets = raw_targets > FIXED_THRESHOLD

    # Compute metrics
    metrics = model_metrics(fixed_targets, fixed_results)
    return metrics

### Train Model

In [11]:
TIMESTAMP = datetime.now().strftime('%Y%m%d%H%M%S')
CHECKPOINT_PATH = os.path.join(ROOT_PATH, 'checkpoints', 'bertimbau-bf16', TIMESTAMP)
MODEL_PATH = os.path.join(ROOT_PATH, 'models', 'bertimbau-bf16', TIMESTAMP)
BEST_MODEL_PATH = os.path.join(MODEL_PATH, 'best_model.pt')
os.makedirs(CHECKPOINT_PATH, exist_ok=True)
os.makedirs(MODEL_PATH, exist_ok=True)

loss_history = []
metric_history = []
test_metric_history = []
target_metric = ('Weighted F2', 'weighted_f2')
best_metric = float('-inf')
best_epoch = 0

# Save the best model; Override checkpoints; Track metrics
def epoch_callback(epoch, avg_loss):
    global loss_history, metric_history, test_metric_history, target_metric, best_metric, best_epoch
    
    metrics = validate_result(validate_loader, model)
    loss_history.append(avg_loss)
    metric_history.append(metrics)
    test_metrics = validate_result(test_loader, model)
    test_metric_history.append(test_metrics)

    print(f'Epoch {epoch+1}: Loss: {avg_loss:.4f}')
    print(f'Validation {target_metric[0]}: {metrics[target_metric[1]]:.4f}')
    print(f'Test {target_metric[0]}: {test_metrics[target_metric[1]]:.4f}')
    
    if metrics[target_metric[1]] > best_metric:
        print(f'New best model found!')
        best_metric = metrics[target_metric[1]]
        best_epoch = epoch
        torch.save(model, BEST_MODEL_PATH)



train_epochs(
    trainer, EPOCHS, model, train_loader, loss_fn, optimizer, PYTORCH_DEVICE,
    checkpoint_path=CHECKPOINT_PATH, epoch_callback=epoch_callback)

Running training epoch 1/20


  0%|          | 0/699 [00:00<?, ?it/s]

  0%|          | 0/88 [00:00<?, ?it/s]

  0%|          | 0/88 [00:00<?, ?it/s]

Epoch 1: Loss: 0.6361
Validation Weighted F2: 0.7883
Test Weighted F2: 0.7842
New best model found!
Finished training epoch 1/20; Average Loss: 0.6361
Running training epoch 2/20


...

Epoch 19: Loss: 0.2608
Validation Weighted F2: 0.7825
Test Weighted F2: 0.7883
Finished training epoch 19/20; Average Loss: 0.2608
Running training epoch 20/20


  0%|          | 0/699 [00:00<?, ?it/s]

  0%|          | 0/88 [00:00<?, ?it/s]

  0%|          | 0/88 [00:00<?, ?it/s]

Epoch 20: Loss: 0.2557
Validation Weighted F2: 0.7839
Test Weighted F2: 0.7847
Finished training epoch 20/20; Average Loss: 0.2557


In [12]:
# Build result metrics data frame per epoch
result_df = pl.DataFrame({
    'epoch': range(1, len(loss_history) + 1),
    'loss': loss_history,
}).with_columns(pl.from_dicts(metric_history))

test_result_df = pl.DataFrame({
    'epoch': range(1, len(loss_history) + 1),
}).with_columns(pl.from_dicts(test_metric_history))

result_df.head()


shape: (5, 9)
┌───────┬──────────┬─────────────┬──────────┬───┬──────────┬──────────┬──────────┬───────────┐
│ epoch ┆ loss     ┆ weighted_f1 ┆ macro_f1 ┆ … ┆ macro_f2 ┆ accuracy ┆ recall   ┆ precision │
│ ---   ┆ ---      ┆ ---         ┆ ---      ┆   ┆ ---      ┆ ---      ┆ ---      ┆ ---       │
│ i64   ┆ f64      ┆ f64         ┆ f64      ┆   ┆ f64      ┆ f64      ┆ f64      ┆ f64       │
╞═══════╪══════════╪═════════════╪══════════╪═══╪══════════╪══════════╪══════════╪═══════════╡
│ 1     ┆ 0.636126 ┆ 0.791011    ┆ 0.781505 ┆ … ┆ 0.787686 ┆ 0.788193 ┆ 0.788193 ┆ 0.802364  │
│ 2     ┆ 0.543765 ┆ 0.804206    ┆ 0.794056 ┆ … ┆ 0.798546 ┆ 0.802147 ┆ 0.802147 ┆ 0.810366  │
│ 3     ┆ 0.499501 ┆ 0.792718    ┆ 0.784253 ┆ … ┆ 0.791817 ┆ 0.789624 ┆ 0.789624 ┆ 0.808785  │
│ 4     ┆ 0.471502 ┆ 0.805076    ┆ 0.795277 ┆ … ┆ 0.800267 ┆ 0.802862 ┆ 0.802862 ┆ 0.812368  │
│ 5     ┆ 0.443094 ┆ 0.809315    ┆ 0.798525 ┆ … ┆ 0.801579 ┆ 0.807871 ┆ 0.807871 ┆ 0.81257   │
└───────┴──────────┴─────────────┴──────────┴───┴──────────┴──────────┴──────────┴───────────┘

In [13]:
# Plot Loss and Target Metric per Epoch, highlighting the peak
fig_a = px.line(result_df, x='epoch', y='loss', title='Loss per Epoch', template='plotly_dark')
fig_a.add_scatter(x=[best_epoch+1], y=[loss_history[best_epoch]], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_a.update_layout()
fig_a.show()

fig_b = px.line(result_df, x='epoch', y='weighted_f2', title='Validation Weighted F2 per Epoch', template='plotly_dark')
fig_b.add_scatter(x=[best_epoch+1], y=[metric_history[best_epoch]['weighted_f2']], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_b.update_layout()
fig_b.show()

fig_c = px.line(test_result_df, x='epoch', y='weighted_f2', title='Test Weighted F2 per Epoch', template='plotly_dark')
fig_c.add_scatter(x=[best_epoch+1], y=[test_metric_history[best_epoch]['weighted_f2']], mode='markers', showlegend=False, marker={'color': 'red', 'size': 10}, name='Best Model')
fig_c.update_layout()
fig_c.show()